In [5]:
import os
os.getcwd()

'/home/jovyan/hddm/temp'

In [6]:
runtime="0"
os.path.exists("./tmp" + runtime)

True

In [1]:
import sys
print('Notebook is running:', sys.executable)

# further check your python version
from platform import python_version

print('The current Python version is', python_version())

# If you are sure that conda is installed, also check the package that install
#!conda list  # list the conda

import hddm, IPython, kabuki, pymc
import numpy as np
import pandas as pd
import seaborn as sns
print('The current HDDM version is', hddm.__version__) # 0.8.0
print('The current Kabuki version is', kabuki.__version__) # 0.6.3
print('The current PyMC version is', pymc.__version__) # 2.3.8

# Warning:`IPython.parallel` package has been deprecated since IPython 4.0. 
print('The current IPython version is', IPython.__version__) 

print('The current Numpy version is', np.__version__) 

print('The current Pandas version is', pd.__version__)

print('The current seaborn version is', sns.__version__)

Notebook is running: /opt/conda/bin/python
The current Python version is 3.7.6
The current HDDM version is 0.8.0
The current Kabuki version is 0.6.3
The current PyMC version is 2.3.8
The current IPython version is 7.15.0
The current Numpy version is 1.19.4
The current Pandas version is 1.0.5
The current seaborn version is 0.11.1


/opt/conda/lib/python3.7/site-packages/IPython/parallel.py:13: ShimWarning: The `IPython.parallel` package has been deprecated since IPython 4.0. You should import from ipyparallel instead.
  "You should import from ipyparallel instead.", ShimWarning)


In [2]:
# Preparation
import os, hddm, time, csv
import glob
import datetime
from datetime import date

import pymc as pm
import hddm
import kabuki

import arviz as az
import numpy as np
import pandas as pd
import feather
import xarray as xr
import matplotlib.pyplot as plt
import seaborn as sns
from patsy import dmatrix

from p_tqdm import p_map
from functools import partial

# set the color of plots
from cycler import cycler
plt.rcParams['axes.prop_cycle'] = cycler(color='bgrcmykw')

In [3]:
# NOTE: I hacked the `post_pred_gen`, 
# more detals: https://groups.google.com/g/hddm-users/c/Is6AM7eN0fo
from post_pred_gen_redifined import _parents_to_random_posterior_sample
from post_pred_gen_redifined import _post_pred_generate
from post_pred_gen_redifined import post_pred_gen

from pointwise_loglik_gen import _pointwise_like_generate
from pointwise_loglik_gen import pointwise_like_gen

# import self-defined functions
from SimData import SimData
from run_models import run_m1, run_m2, run_m4, run_m5, run_m7

model_func = [run_m1, run_m2, run_m4, run_m5, run_m7]

m_keys = ["ms1",
          "ms2",
          "ms4",
          "ms5",
          "ms7"]

df_keys = ["sim_df1", 
           "sim_df2", 
           "sim_df4", 
           "sim_df5",
           "sim_df7"]


In [5]:
def model_recov(data=None, m_keys=None, model_func=None):
    """
    This func is for model recovery. 
    
    data: input data, can be simulated data or real data
    m_keys: id for different models, which is used as the key for the model_func.
    model_func: a list of model functions
    
    This function will fit the data with all models in the model_func
    
    """
    InfData = {}
    models = {}
    for ii in range(len(m_keys)):
        m_key = m_keys[ii]

        ### Run models
        save_name = "./tmp0/" + m_key + "_tmp"
        print("start model fitting for ", m_key)
        ms_tmp = p_map(partial(model_func[ii], 
                               df=data, 
                               samples=samples,
                               burn=burn,
                               save_name=save_name),
                       range(chains))

        ### Observations
        xdata_observed = ms_tmp[0].data.copy()
        xdata_observed.index.names = ['trial_idx']
        xdata_observed = xdata_observed[['rt', 'response']]
        xdata_observed = xr.Dataset.from_dataframe(xdata_observed)

        ### posteriors
        xdata_posterior = []
        for jj in range(len(ms_tmp)):
            trace_tmp = ms_tmp[jj].get_traces()
            trace_tmp['chain'] = jj
            trace_tmp['draw'] = np.arange(len(trace_tmp), dtype=int)
            xdata_posterior.append(trace_tmp)
        xdata_posterior = pd.concat(xdata_posterior)
        xdata_posterior = xdata_posterior.set_index(["chain", "draw"])
        xdata_posterior = xr.Dataset.from_dataframe(xdata_posterior)

        ### PPC
        xdata_post_pred = [] # define an empty dict    
        print("start PPC for ", m_key)
        start_time = time.time()  
        xdata_post_pred = p_map(partial(post_pred_gen), ms_tmp)
        print("Running PPC for ", m_key, " costs %f seconds" % (time.time() - start_time))
        xdata_post_pred = pd.concat(xdata_post_pred, names=['chain'], 
                                keys = list(range(len(xdata_post_pred))))
        xdata_post_pred = xdata_post_pred.reset_index(level=1, drop=True)
        xdata_post_pred = xr.Dataset.from_dataframe(xdata_post_pred)

        ### Point-wise log likelihood
        xdata_loglik = [] # define an empty dict
        print("start calculating loglik for ", m_key)
        start_time = time.time()  # the start time of the processing
        xdata_loglik = p_map(partial(pointwise_like_gen), ms_tmp)
        print("Generating loglik costs %f seconds" % (time.time() - start_time))

        xdata_loglik = pd.concat(xdata_loglik, names=['chain'], 
                                keys = list(range(len(xdata_loglik))))
        xdata_loglik = xdata_loglik.reset_index(level=1, drop=True)
        xdata_loglik = xr.Dataset.from_dataframe(xdata_loglik)
        
        ### convert to InfData
        InfData[m_key] = az.InferenceData(posterior=xdata_posterior, 
                                                 observed_data=xdata_observed,
                                                 posterior_predictive=xdata_post_pred,
                                                 log_likelihood = xdata_loglik)
        models[m_key] = ms_tmp
    return models, InfData

In [4]:
samples = 200
burn = 100
chains = 4

In [6]:
%%time

conf_mat_dic0 = pd.DataFrame(0, index=m_keys, columns=df_keys)
conf_mat_loo0 = pd.DataFrame(0, index=m_keys, columns=df_keys)
conf_mat_waic0 = pd.DataFrame(0, index=m_keys, columns=df_keys)

for sim in range (4):   
    for df_key in df_keys:
        ### simulate data
        data = SimData(df_key)

        ### fit the sim data
        print("Start model recovery for ", df_key)
        models, InfData = model_recov(data=data, m_keys=m_keys, model_func=model_func)

        ### compare models
        tmp_loo_comp = az.compare(InfData, ic="loo")
        tmp_loo_comp = tmp_loo_comp.reset_index()
        tmp_waic_comp = az.compare(InfData, ic="waic")
        tmp_waic_comp = tmp_waic_comp.reset_index()
        
        tmp_dic = []
        indx_name = []

        for m_key, model in models.items():
            m_tmp = kabuki.utils.concat_models(model)
            tmp_dic.append(m_tmp.dic)
            indx_name.append(m_key)
            
        tmp_dic_comp = pd.DataFrame(tmp_dic, index=indx_name, columns=['dic'])
        tmp_dic_comp = tmp_dic_comp.sort_values(by=['dic'])
        tmp_dic_comp = tmp_dic_comp.reset_index()
        #conf_mat_dic.rename(columns={'index':'rank'}, inplace=True)

        ### record the best models
        conf_mat_dic0.loc[tmp_dic_comp.loc[0, 'index'], df_key] += 1
        conf_mat_loo0.loc[tmp_loo_comp.loc[0, 'index'], df_key] += 1
        conf_mat_waic0.loc[tmp_waic_comp.loc[0, 'index'], df_key] += 1

        conf_mat_dic0.to_csv('conf_mat_dic0.csv')
        conf_mat_loo0.to_csv('conf_mat_loo0.csv')
        conf_mat_waic0.to_csv('conf_mat_waic0.csv')

Start model recovery for  sim_df1
start model fitting for  ms1


/opt/conda/lib/python3.7/site-packages/pandas/core/indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)


/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:2149: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)
/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:2149: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)
/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:2149: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)
/opt/conda/lib/python3.7/site-packages/scipy/optimize/optimize.py:2149: RuntimeWarning: invalid value encountered in double_scalars
  tmp2 = (x - v) * (fx - fw)


 [                  1%                  ] 3 of 200 complete in 0.7 sec[                  1%                  ] 3 of 200 complete in 0.8 sec[                  1%                  ] 3 of 200 complete in 0.7 sec[                  1%                  ] 3 of 200 complete in 0.9 sec[                  2%                  ] 4 of 200 complete in 1.2 sec[                  2%                  ] 4 of 200 complete in 1.4 sec[                  2%                  ] 4 of 200 complete in 1.4 sec[                  2%                  ] 4 of 200 complete in 1.4 sec[                  2%                  ] 5 of 200 complete in 2.0 sec[                  2%                  ] 5 of 200 complete in 1.9 sec[-                 3%                  ] 6 of 200 complete in 2.2 sec[-                 3%                  ] 6 of 200 complete in 2.4 sec[-                 3%                  ] 6 of 200 complete in 2.5 sec[-                 3%                  ] 6 of 200 complete in 2.4 sec[-                 3%            

 [-------          18%                  ] 37 of 200 complete in 19.4 sec[-------          19%                  ] 38 of 200 complete in 19.7 sec[-------          19%                  ] 38 of 200 complete in 19.8 sec[-------          19%                  ] 38 of 200 complete in 20.0 sec[-------          19%                  ] 39 of 200 complete in 20.2 sec[-------          20%                  ] 40 of 200 complete in 20.4 sec[-------          19%                  ] 39 of 200 complete in 20.5 sec[-------          20%                  ] 40 of 200 complete in 20.7 sec[-------          20%                  ] 40 of 200 complete in 20.8 sec[-------          20%                  ] 41 of 200 complete in 21.0 sec[-------          20%                  ] 41 of 200 complete in 21.3 sec[-------          20%                  ] 41 of 200 complete in 21.3 sec[-------          21%                  ] 42 of 200 complete in 21.5 sec[-------          20%                  ] 41 of 200 complete in 21.5 sec[----

...

 [                  1%                  ] 2 of 200 complete in 0.6 sec[                  1%                  ] 2 of 200 complete in 0.8 sec[                  1%                  ] 3 of 200 complete in 1.4 sec[                  1%                  ] 3 of 200 complete in 1.5 sec[                  1%                  ] 3 of 200 complete in 1.5 sec[                  1%                  ] 3 of 200 complete in 1.9 sec[                  2%                  ] 4 of 200 complete in 2.2 sec[                  2%                  ] 4 of 200 complete in 2.4 sec[                  2%                  ] 4 of 200 complete in 2.5 sec[                  2%                  ] 4 of 200 complete in 3.0 sec[                  2%                  ] 5 of 200 complete in 3.2 sec[                  2%                  ] 5 of 200 complete in 3.5 sec[                  2%                  ] 5 of 200 complete in 3.5 sec[                  2%                  ] 5 of 200 complete in 4.2 sec[-                 3%            

 -----------      29%                  ] 59 of 200 complete in 66.0 secc[------           16%                  ] 32 of 200 complete in 31.9 sec[------           16%                  ] 32 of 200 complete in 32.1 sec[-----            15%                  ] 31 of 200 complete in 32.5 sec[------           16%                  ] 33 of 200 complete in 33.1 sec[------           16%                  ] 33 of 200 complete in 33.2 sec[------           16%                  ] 33 of 200 complete in 33.2 sec[------           16%                  ] 32 of 200 complete in 33.6 sec[------           17%                  ] 34 of 200 complete in 34.1 sec[------           17%                  ] 34 of 200 complete in 34.2 sec[------           17%                  ] 34 of 200 complete in 34.4 sec[------           16%                  ] 33 of 200 complete in 34.7 sec[------           17%                  ] 35 of 200 complete in 35.2 sec[------           17%                  ] 35 of 200 complete in 35.3 sec[----

 [-----------      30%                  ] 60 of 200 complete in 66.8 sec[-----------      30%                  ] 60 of 200 complete in 67.1 sec[-----------      31%                  ] 62 of 200 complete in 67.1 sec[-----------      31%                  ] 62 of 200 complete in 67.6 sec[-----------      30%                  ] 61 of 200 complete in 68.2 sec[-----------      31%                  ] 63 of 200 complete in 68.2 sec[-----------      30%                  ] 61 of 200 complete in 68.2 sec[-----------      31%                  ] 63 of 200 complete in 68.9 sec[-----------      31%                  ] 62 of 200 complete in 69.4 sec[------------     32%                  ] 64 of 200 complete in 69.4 sec[-----------      31%                  ] 62 of 200 complete in 69.6 sec[------------     32%                  ] 64 of 200 complete in 70.2 sec[------------     32%                  ] 65 of 200 complete in 70.5 sec[-----------      31%                  ] 63 of 200 complete in 70.6 sec[----

 [---------------- 44%                  ] 89 of 200 complete in 101.6 sec[-----------------47%                  ] 95 of 200 complete in 102.3 sec[-----------------45%                  ] 90 of 200 complete in 102.4 sec[-----------------45%                  ] 90 of 200 complete in 102.8 sec[---------------- 43%                  ] 86 of 200 complete in 102.6 sec[-----------------48%                  ] 96 of 200 complete in 103.4 sec[-----------------45%                  ] 91 of 200 complete in 103.7 sec[-----------------45%                  ] 91 of 200 complete in 103.9 sec[---------------- 43%                  ] 87 of 200 complete in 104.0 sec[-----------------48%                  ] 97 of 200 complete in 104.5 sec[-----------------46%                  ] 92 of 200 complete in 104.7 sec[-----------------46%                  ] 92 of 200 complete in 105.1 sec[-----------------49%                  ] 98 of 200 complete in 105.5 sec[---------------- 44%                  ] 88 of 200 complete in 

 [-----------------58%--                ] 116 of 200 complete in 135.7 sec[-----------------58%--                ] 117 of 200 complete in 135.8 sec[-----------------56%-                 ] 112 of 200 complete in 135.8 sec[-----------------64%----              ] 128 of 200 complete in 136.1 sec[-----------------58%--                ] 117 of 200 complete in 137.0 sec[-----------------59%--                ] 118 of 200 complete in 137.1 sec[-----------------56%-                 ] 113 of 200 complete in 137.0 sec[-----------------64%----              ] 129 of 200 complete in 137.2 sec[-----------------65%----              ] 130 of 200 complete in 138.2 sec[-----------------59%--                ] 118 of 200 complete in 138.3 sec[-----------------59%--                ] 119 of 200 complete in 138.3 sec[-----------------57%-                 ] 114 of 200 complete in 138.3 sec[-----------------65%----              ] 131 of 200 complete in 139.2 sec[-----------------59%--                ] 119 of 20

In [7]:
tmp_loo_comp

In [ ]:
tmp_waic_comp

In [ ]:
models['ms7'][0].plot_posteriors()